#Predviđanje cijena rabljenih automobila



#Uvod, cilj i podaci

##Uvod
Automobilsko tržište rabljenih vozila jedno je od dinamičnih područja u kojem mnogi čimbenici utječu na cijene vozila. Kupci i prodavatelji često su suočeni s izazovom procjene pravih vrijednosti vozila, što dovodi do potrebe za razvojem preciznih modela predviđanja cijena rabljenih automobila. U ovom projektu, istražit ćemo različite značajke automobila i njihov utjecaj na cijene, koristeći strojno učenje kako bismo stvorili model koji će pomoći u predviđanju cijena rabljenih automobila.

##Cilj
Cilj ovog projekta je izraditi model strojnog učenja koji će na temelju različitih atributa rabljenih automobila predviđati njihove cijene. Kroz analizu i obradu podataka, istražit ćemo koje su značajke ključne za određivanje cijene vozila te kako te značajke međusobno utječu. Konačni model trebao bi omogućiti korisnicima, kao što su kupci i prodavatelji, bolje razumijevanje tržišta rabljenih automobila te im pružiti informacije koje će im pomoći u donošenju informiranih odluka prilikom kupnje ili prodaje vozila. Ovaj projekt ima potencijal poboljšati transparentnost na tržištu rabljenih automobila i olakšati poslovanje u automobilskoj industriji.

##Podaci
Podaci su preuzeti s platforme Kaggle i obuhvaćaju 30 stupaca s ukupno 38 531 zapisa. Podaci pružaju informacije o cijeni rabljenih automobila ovisno o karakteristikama istih, kao što su: godina proizvodnje, prijeđeni kilometri, tip motora i slično.

In [ ]:
# @title Import potrebnih biblioteka

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from google.colab import drive
import warnings
import plotly.express as px

warnings.simplefilter(action='ignore', category=FutureWarning)
pd.options.mode.chained_assignment = None

In [ ]:
#@title Učitavanje biblioteke za interaktivnih vizualizaciju podataka
!pip install plotly

In [ ]:
# @title Spajanje na Google Drive
from google.colab import drive
drive.mount("/content/drive")

Mounted at /content/drive


#Učitavanje i priprema podataka


In [ ]:
# @title Učitavanje podataka s Google Drive-a

%cd /content/drive/MyDrive/PMF/1.SEM/ZNANSTVENO_PROGRAMIRANJE/PROJEKT
df=pd.read_csv("./cars.csv")

#df=pd.read_csv("/content/drive/MyDrive/_Projekt_ZP/cars.csv")

/content/drive/MyDrive/PMF/1.SEM/ZNANSTVENO_PROGRAMIRANJE/PROJEKT


##Osnovne informacije o podacima
Podaci se sastoje od 30 stupaca (atributa) koji opisuju tržište rabljenih automobila. S obzirom da za neke podatke nemamo točne informacije što predstavljaju, a i za daljnju analizu nam nisu potrebni svi podaci, koristit ćemo samo dolje navedene stupce.

| Redni broj | Naziv na engleskom | Naziv na hrvatskom |
|------------|--------------------|---------------------|
| 0          | manufacturer_name  | marka               | Naziv proizvođača                          |
| 1          | model_name         | model               | Naziv modela                               |
| 2          | transmission       | transmisija         | Tip prijenosa                              |
| 3          | odometer_value     | kilometraža         | Stanje brojača kilometara                 |
| 4          | year_produced      | godina              | Godina proizvodnje                         |
| 5          | engine_fuel        | gorivo              | Tip goriva                                |
| 6          | engine_capacity    | kapacitet           | Zapremina motora                           |
| 7          | price_usd          | cijena_€            | Cijena u američkim dolarima               |
    





In [ ]:
df.shape

(38531, 30)

In [ ]:
df.head()

manufacturer_name model_name transmission   color  odometer_value  \
0            Subaru    Outback    automatic  silver          190000   
1            Subaru    Outback    automatic    blue          290000   
2            Subaru   Forester    automatic     red          402000   
3            Subaru    Impreza   mechanical    blue           10000   
4            Subaru     Legacy    automatic   black          280000   

   year_produced engine_fuel  engine_has_gas engine_type  engine_capacity  \
0           2010    gasoline           False    gasoline              2.5   
1           2002    gasoline           False    gasoline              3.0   
2           2001    gasoline           False    gasoline              2.5   
3           1999    gasoline           False    gasoline              3.0   
4           2001    gasoline           False    gasoline              2.5   

   ... feature_1  feature_2 feature_3 feature_4  feature_5  feature_6  \
0  ...      True       True      True     False       True      False   
1  ...      True      False     False      True       True      False   
2  ...      True      False     False     False      False      False   
3  ...     False      False     False     False      False      False   
4  ...      True      False      True      True      False      False   

  feature_7  feature_8  feature_9  duration_listed  
0      True       True       True               16  
1     False      False       True               83  
2     False       True       True              151  
3     False      False      False               86  
4     False      False       True                7  

[5 rows x 30 columns]

In [ ]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 38531 entries, 0 to 38530
Data columns (total 30 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   manufacturer_name  38531 non-null  object 
 1   model_name         38531 non-null  object 
 2   transmission       38531 non-null  object 
 3   color              38531 non-null  object 
 4   odometer_value     38531 non-null  int64  
 5   year_produced      38531 non-null  int64  
 6   engine_fuel        38531 non-null  object 
 7   engine_has_gas     38531 non-null  bool   
 8   engine_type        38531 non-null  object 
 9   engine_capacity    38521 non-null  float64
 10  body_type          38531 non-null  object 
 11  has_warranty       38531 non-null  bool   
 12  state              38531 non-null  object 
 13  drivetrain         38531 non-null  object 
 14  price_usd          38531 non-null  float64
 15  is_exchangeable    38531 non-null  bool   
 16  location_region    385

In [ ]:
df.describe()

odometer_value  year_produced  engine_capacity     price_usd  \
count    38531.000000   38531.000000     38521.000000  38531.000000   
mean    248864.638447    2002.943734         2.055161   6639.971021   
std     136072.376530       8.065731         0.671178   6428.152018   
min          0.000000    1942.000000         0.200000      1.000000   
25%     158000.000000    1998.000000         1.600000   2100.000000   
50%     250000.000000    2003.000000         2.000000   4800.000000   
75%     325000.000000    2009.000000         2.300000   8990.000000   
max    1000000.000000    2019.000000         8.000000  50000.000000   

       number_of_photos    up_counter  duration_listed  
count      38531.000000  38531.000000     38531.000000  
mean           9.649062     16.306091        80.577249  
std            6.093217     43.286933       112.826569  
min            1.000000      1.000000         0.000000  
25%            5.000000      2.000000        23.000000  
50%            8.000000      5.000000        59.000000  
75%           12.000000     16.000000        91.000000  
max           86.000000   1861.000000      2232.000000

In [ ]:
razliciti_modeli = df['manufacturer_name'].unique()
print(f"Raspolažemo s {razliciti_modeli.shape} različitih modela, od kojih su neki: {razliciti_modeli}.")

Raspolažemo s (55,) različitih modela, od kojih su neki: ['Subaru' 'LADA' 'Dodge' 'УАЗ' 'Kia' 'Opel' 'Москвич' 'Alfa Romeo' 'Acura'
 'Dacia' 'Lexus' 'Mitsubishi' 'Lancia' 'Citroen' 'Mini' 'Jaguar' 'Porsche'
 'SsangYong' 'Daewoo' 'Geely' 'ВАЗ' 'Fiat' 'Ford' 'Renault' 'Seat' 'Rover'
 'Volkswagen' 'Lifan' 'Jeep' 'Cadillac' 'Audi' 'ЗАЗ' 'Toyota' 'ГАЗ'
 'Volvo' 'Chevrolet' 'Great Wall' 'Buick' 'Pontiac' 'Lincoln' 'Hyundai'
 'Nissan' 'Suzuki' 'BMW' 'Mazda' 'Land Rover' 'Iveco' 'Skoda' 'Saab'
 'Infiniti' 'Chery' 'Honda' 'Mercedes-Benz' 'Peugeot' 'Chrysler'].


##Obrada podataka
Provjeravamo postoje li duplikati u podacima.

**Zaključak:** Uklanjamo duplicirane podatke.

In [ ]:
column_names = df.columns.tolist()

print("Column Names:")
print(column_names)

Column Names:
['manufacturer_name', 'model_name', 'transmission', 'color', 'odometer_value', 'year_produced', 'engine_fuel', 'engine_has_gas', 'engine_type', 'engine_capacity', 'body_type', 'has_warranty', 'state', 'drivetrain', 'price_usd', 'is_exchangeable', 'location_region', 'number_of_photos', 'up_counter', 'feature_0', 'feature_1', 'feature_2', 'feature_3', 'feature_4', 'feature_5', 'feature_6', 'feature_7', 'feature_8', 'feature_9', 'duration_listed']


In [ ]:
# @title Uklanjanje nepotrebnih stupaca

columns_to_remove = ["color", "engine_has_gas","body_type","engine_type","has_warranty","state","drivetrain","is_exchangeable","location_region","number_of_photos","up_counter","feature_0","feature_1","feature_2","feature_3",
                     "feature_4","feature_5","feature_6","feature_7","feature_8","feature_9","duration_listed"]


df = df.drop(columns=columns_to_remove)
df.head()

manufacturer_name model_name transmission  odometer_value  year_produced  \
0            Subaru    Outback    automatic          190000           2010   
1            Subaru    Outback    automatic          290000           2002   
2            Subaru   Forester    automatic          402000           2001   
3            Subaru    Impreza   mechanical           10000           1999   
4            Subaru     Legacy    automatic          280000           2001   

  engine_fuel  engine_capacity  price_usd  
0    gasoline              2.5   10900.00  
1    gasoline              3.0    5000.00  
2    gasoline              2.5    2800.00  
3    gasoline              3.0    9999.00  
4    gasoline              2.5    2134.11

###DOVRSIT - Mapiranje podataka
Numeričko kodiranje kategoričkih varijabli olakšati će nam daljni rad s podacima i poboljšati performanse modela. Stoga provjeravamo koje podatke možemo zapisati u obliku numeričkih podataka te vršimo zamjenu.

In [ ]:
# @title Mapiranje kategoričkih podataka

# Vrijednosti stupca engine_fuel
engine_fuel_values = df["engine_fuel"].unique()
print("\nVrijednosti stupca engine_fuel:")
print(engine_fuel_values)


Vrijednosti stupca engine_fuel:
['gasoline' 'gas' 'diesel' 'hybrid-petrol' 'hybrid-diesel' 'electric']


In [ ]:
engine_fuel_mapping={"gasoline":0,"gas":1,"diesel":2,"hybrid-petrol":3,"hybrid-diesel":4,"electric":5}
df["engine_fuel"]=df["engine_fuel"].map(engine_fuel_mapping)

df.head()

manufacturer_name model_name transmission  odometer_value  year_produced  \
0            Subaru    Outback    automatic          190000           2010   
1            Subaru    Outback    automatic          290000           2002   
2            Subaru   Forester    automatic          402000           2001   
3            Subaru    Impreza   mechanical           10000           1999   
4            Subaru     Legacy    automatic          280000           2001   

   engine_fuel  engine_capacity  price_usd  
0            0              2.5   10900.00  
1            0              3.0    5000.00  
2            0              2.5    2800.00  
3            0              3.0    9999.00  
4            0              2.5    2134.11

In [ ]:
# @title Kilometraža
import math

def round_to_first_two_digits(n):
    if n == 0:
        return 0

    # Broj znamenaka u broju
    digits = math.floor(math.log10(n)) + 1

    # Faktor za skaliranje broja tako da ima samo dvije značajne cifre
    scale = 10 ** (digits - 2)

    # Zaokruživanje broja na prve dvije značajne cifre
    return round(n / scale) * scale


# Primijenite funkciju na stupac "kilometraza"
df["zaokruzena_kilometraza"] = df["odometer_value"].apply(round_to_first_two_digits)

df = df.drop("odometer_value", axis=1)


###Promjena naziva stupca

In [ ]:
column_name_mapping = {"manufacturer_name": "marka", "model_name": "model", "zaokruzena_kilometraza": "kilometraža", "engine_fuel":"gorivo", "engine_capacity":"kapacitet", "price_usd":"cijena","year_produced":"godina","transmission":"transmisija"}
# column_name_mapping = {"manufacturer_name": "marka", "model_name": "model", "zaokruzena_kilometraza": "kilometraža", "engine_fuel":"gorivo", "engine_capacity":"kapacitet", "price_usd":"cijena","Godine Kategorija":"godine","transmission":"transmisija"}


df = df.rename(columns=column_name_mapping)

df.head()

marka     model transmisija  godina  gorivo  kapacitet    cijena  \
0  Subaru   Outback   automatic    2010       0        2.5  10900.00   
1  Subaru   Outback   automatic    2002       0        3.0   5000.00   
2  Subaru  Forester   automatic    2001       0        2.5   2800.00   
3  Subaru   Impreza  mechanical    1999       0        3.0   9999.00   
4  Subaru    Legacy   automatic    2001       0        2.5   2134.11   

   kilometraža  
0     190000.0  
1     290000.0  
2     400000.0  
3      10000.0  
4     280000.0

###Pretvraranje cijene u EUR

In [ ]:
#pretvaranje cijene u EUR
usd_to_eur_exchange_rate = 0.91
df["cijena_€"] = df["cijena"] * usd_to_eur_exchange_rate

#uklanjanje stupca s cijenom u dolarima
df = df.drop("cijena", axis=1)

#zaokruživanje iznosa na dvije decimale
df['cijena_€'] = df['cijena_€'].round(2)

df.head()

marka     model transmisija  godina  gorivo  kapacitet  kilometraža  \
0  Subaru   Outback   automatic    2010       0        2.5     190000.0   
1  Subaru   Outback   automatic    2002       0        3.0     290000.0   
2  Subaru  Forester   automatic    2001       0        2.5     400000.0   
3  Subaru   Impreza  mechanical    1999       0        3.0      10000.0   
4  Subaru    Legacy   automatic    2001       0        2.5     280000.0   

   cijena_€  
0   9919.00  
1   4550.00  
2   2548.00  
3   9099.09  
4   1942.04

###Rješavanje NaN podataka
Provjeravamo postoje li redci s NaN vrijednostima u redcima i stupcima

In [ ]:
# @title Provjeravamo postoje li NaN redci
print("Broj NaN vrijednosti podataka po stupcima:")
print(df.isnull().sum())

# Ispisi retke koji se sastoje samo od NaN vrijednosti
print("\nRedovi koji se sastoje samo od NaN vrijednosti:")
print(df[df.isnull().all(axis=1)])

# Izbaci retke čiji su svi elementi NaN
df = df.dropna(how="all")

Broj NaN vrijednosti podataka po stupcima:
marka           0
model           0
transmisija     0
godina          0
gorivo          0
kapacitet      10
kilometraža     0
cijena_€        0
dtype: int64

Redovi koji se sastoje samo od NaN vrijednosti:
Empty DataFrame
Columns: [marka, model, transmisija, godina, gorivo, kapacitet, kilometraža, cijena_€]
Index: []


In [ ]:
# @title Provjeravamo postoje li NaN vrijednosti u preostalim podacima
# Izbaci retke čiji su svi elementi NaN
df_nan = df.dropna(how='all')

# Ispisi retke gdje postoje NaN vrijednosti
print("Redovi s barem jednom NaN vrijednosti:")
print(df_nan[df_nan.isnull().any(axis=1)])

Redovi s barem jednom NaN vrijednosti:
           marka model transmisija  godina  gorivo  kapacitet  kilometraža  \
8782        Fiat   500   automatic    2013       5        NaN      27000.0   
9048        Fiat   500   automatic    2014       5        NaN      49000.0   
24226  Chevrolet  Volt   automatic    2013       5        NaN     170000.0   
25943     Nissan  Leaf   automatic    2015       5        NaN      57000.0   
26203     Nissan  Leaf   automatic    2011       5        NaN      97000.0   
26222     Nissan  Leaf   automatic    2014       5        NaN      50000.0   
26582     Nissan  Leaf   automatic    2014       5        NaN      84000.0   
26914     Nissan  Leaf   automatic    2013       5        NaN      84000.0   
27554        BMW    i3   automatic    2015       5        NaN      54000.0   
29590        BMW    i3   automatic    2018       5        NaN      67000.0   

       cijena_€  
8782   13559.00  
9048   14560.00  
24226  11784.50  
25943  12603.50  
26203   8463

In [ ]:
# @title Popunjavanje NaN vrijednosti

# Popunjavanje NaN vrijednosti
mean_value = df['kapacitet'].mean()
df['kapacitet'].fillna(mean_value, inplace=True)

# df = df.dropna()

###Duplicirani podaci

In [ ]:
# Provjeri duplicirane retke
duplicates = df[df.duplicated()]

# Ukupan broj dupliciranih redova
num_duplicates = df.duplicated().sum()
print(f"Ukupan broj dupliciranih redova: {num_duplicates}")

# Ispisi duplicirane retke
print("Duplicirani redovi:")
print(duplicates)


# Ukloni duplicirane retke
df = df.drop_duplicates()

# Ponovno provjeri ukupan broj dupliciranih redova
num_duplicates_after_removal = df.duplicated().sum()
print(f"Ukupan broj dupliciranih redova nakon uklanjanja: {num_duplicates_after_removal}")


Ukupan broj dupliciranih redova: 437
Duplicirani redovi:
          marka          model transmisija  godina  gorivo  kapacitet  \
145      Subaru         Legacy   automatic    2004       0        2.5   
611       Dodge  Grand Caravan  mechanical    2008       0        3.3   
662       Dodge           Dart   automatic    2012       0        2.0   
1011        Kia         Clarus  mechanical    1999       1        2.0   
1899       Opel          Astra  mechanical    2010       0        1.4   
...         ...            ...         ...     ...     ...        ...   
37989   Peugeot            407  mechanical    2005       2        1.6   
37991   Peugeot            406  mechanical    1997       0        1.8   
38215  Chrysler        Voyager   automatic    2001       1        2.4   
38365  Chrysler   Town&Country   automatic    2004       0        3.3   
38399  Chrysler           Neon  mechanical    1997       0        2.0   

       kilometraža  cijena_€  
145       350000.0   4095.00  
611 

##Konačan prikaz podataka

In [ ]:
print(df.info())
print()
df.head()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 38094 entries, 0 to 38530
Data columns (total 8 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   marka        38094 non-null  object 
 1   model        38094 non-null  object 
 2   transmisija  38094 non-null  object 
 3   godina       38094 non-null  int64  
 4   gorivo       38094 non-null  int64  
 5   kapacitet    38094 non-null  float64
 6   kilometraža  38094 non-null  float64
 7   cijena_€     38094 non-null  float64
dtypes: float64(3), int64(2), object(3)
memory usage: 2.6+ MB
None



marka     model transmisija  godina  gorivo  kapacitet  kilometraža  \
0  Subaru   Outback   automatic    2010       0        2.5     190000.0   
1  Subaru   Outback   automatic    2002       0        3.0     290000.0   
2  Subaru  Forester   automatic    2001       0        2.5     400000.0   
3  Subaru   Impreza  mechanical    1999       0        3.0      10000.0   
4  Subaru    Legacy   automatic    2001       0        2.5     280000.0   

   cijena_€  
0   9919.00  
1   4550.00  
2   2548.00  
3   9099.09  
4   1942.04

###Vizualizacija podataka
Iz dole prikazanih grafova, možemo pobliže objasniti sa kakvim podacima radimo.

In [ ]:
# @title Matrica korelacije

import plotly.figure_factory as ff


correlation_matrix = df.corr().round(2)

fig = ff.create_annotated_heatmap(
    z=correlation_matrix.values,
    x=list(correlation_matrix.columns),
    y=list(correlation_matrix.index),
    colorscale="Viridis",
    colorbar=dict(title="Correlation Coefficient")
)

fig.update_layout(title="Interactive Correlation Matrix")

fig.show()

Iz ove matrice korelacije očitavamo međusobne odnose vrijednosti iz pojedinih stupaca, odnosno njihovu bitnost u daljnjem predviđanju. Matrica u našem slučaju potvrđiva ono što zapravo već zdravim razumom zaključujemo, a to su odnosi najbitnijih karakteristika polovnih automobila s njihovom cijenom.

In [ ]:
# @title Grafički prikaz numeričkih podataka

import plotly.subplots as sp
import plotly.graph_objects as go

# Kreiranje subplot-a
fig = sp.make_subplots(rows=3, cols=3, subplot_titles=df.select_dtypes(include=['number']).columns)

# Dodavanje histogramskih trace-ova za svaki numerički atribut
for i, col in enumerate(df.select_dtypes(include=['number']).columns):
    trace = go.Histogram(x=df[col], nbinsx=20, name=col)
    fig.add_trace(trace, row=(i // 3) + 1, col=(i % 3) + 1)

# Podešavanje izgleda i naslova
fig.update_layout(title_text='Distribucija numeričkih podataka', showlegend=False)

# Prikazivanje grafikona
fig.show()

Iz ovog grafa očitavamo neku osnovnu opisnu statistiku.


*    Histogram za "godina" pokazuje distribuciju godina proizvodnje automobila. Većina automobila u skupu podataka čini se da je proizvedena nakon 2000. godine, s vrlo malo automobila proizvedenih prije toga. Postoji vidljiv vrhunac koji se možda događa oko 2010-ih, što sugerira da u skupu podataka postoji visoka koncentracija automobila iz tog razdoblja.
*    Stupci pokazuju broj automobila za svaku kategoriju goriva. Vidimo dva vrha, gdje prvi stupac "benzin" ima najveći broj automobila, a treći stupac "hibrid" ima znatno manji broj automobila. Drugi stupac "plin" ima najmanji broj automobila.
*  Ovaj histogram prikazuje distribuciju kapaciteta motora automobila. Čini se da većina automobila ima motore kapaciteta između 1.0 i 2.0.
*   Histogram prikazuje distribuciju automobila po pređenim kilometrima. Većina automobila ima pređenu kilometražu između 0 i 500.000 kilometara, s najvećim brojem automobila koji su prešli manje od 250.000 kilometara.
*   Ovaj histogram prikazuje distribuciju cijena automobila u eurima. Većina automobila ima cijenu ispod 20.000 eura, s najvećim brojem automobila koji koštaju između 0 i 10.000 eura.








In [ ]:
# @title Odnos tipa goriva i transmisije na cijenu

import plotly.subplots as sp
import plotly.graph_objects as go

# Kreiranje subplot-a
fig = sp.make_subplots(rows=1, cols=2, subplot_titles=("Box Plot - odnos tipa goriva i cijene", "Box Plot - odnos transmisije i cijene"))

# Prvi subplot - odnos tipa goriva i cijene
trace1 = go.Box(x=df["gorivo"], y=df["cijena_€"], name="Box Plot - gorivo")
fig.add_trace(trace1, row=1, col=1)

# Drugi subplot - odnos transmisije i cijene
trace2 = go.Box(x=df["transmisija"], y=df["cijena_€"], name="Box Plot - transmisija")
fig.add_trace(trace2, row=1, col=2)

# Podešavanje izgleda i naslova
fig.update_layout(title_text="Odnos tipa goriva i transmisije na cijenu", showlegend=False)

# Prikazivanje grafikona
fig.show()



*   Sve kategorije imaju različite distribucije cijena. Kategorija '0' ima najširu distribuciju cijena s nekoliko izvanrednih točaka (outliers) koje seže do 40k, što sugerira da postoji nekoliko vrlo skupih benzinskih automobila. Dizel npr. također ima široku distribuciju cijena, ali s manje izvanrednih točaka iznad gornjeg kvartila.
*   Automobili s mehaničkom transmisijom imaju uži raspon cijena i niži medijan. Također, postoji nekoliko izvanrednih točaka, ali one ne dosežu visine onih kod automatske transmisije. Automobili s automatskom transmisijom imaju širi raspon cijena, s većim medijanom i više izvanrednih točaka, što ukazuje na to da mogu biti skuplji od onih s mehaničkom transmisijom.



Negativna korelacija između godine i cijene (€): Koeficijent -0.48 ukazuje na umjerenu negativnu korelaciju između starosti vozila (godina) i cijene. To znači da starija vozila imaju tendenciju biti jeftinija.

Pozitivna korelacija između godine i kilometraže: Koeficijent -0.48 sugerira da starija vozila imaju tendenciju imati veću kilometražu.

Pozitivna korelacija između godine i kapaciteta: Koeficijent 0.01 sugerira da postoji vrlo slaba pozitivna korelacija između starosti vozila i kapaciteta.

Pozitivna korelacija između godine i goriva: Koeficijent 0.03 ukazuje na slabu pozitivnu korelaciju između starosti vozila i vrste goriva.

Negativna korelacija između godine i kilometraže: Koeficijent -0.41 sugerira umjerenu negativnu korelaciju između godina i cijene. To znači da starija vozila imaju tendenciju biti jeftinija.

Pozitivna korelacija između godine i cijene (€): Koeficijent 0.70 ukazuje na snažnu pozitivnu korelaciju između starosti vozila i cijene. Starija vozila imaju tendenciju biti skuplja.

Pozitivna korelacija između kapaciteta i cijene (€): Koeficijent 0.30 ukazuje na umjerenu pozitivnu korelaciju između kapaciteta vozila i cijene.

In [ ]:
# @title Utjecaj kapaciteta motora i godine proizvodnje na cijenu

#Odnos godine proizvodnje i cijene
fig = px.scatter(df, x='godina', y='cijena_€', color='godina', size='kilometraža',
                 hover_data=['marka', 'model'], title='Odnos godine proizvodnje i cijene',
                 labels={'godina': 'Godina proizvodnje', 'cijena_€': 'Cijena (€)', 'kilometraža': 'Kilometraža'})

fig.update_layout(
    xaxis=dict(title_text='Godina proizvodnje', tickvals=df['godina'].unique(), ticktext=df['godina'].unique())
)

fig.show()


#Odnos kapaciteta motora i cijene
fig = px.scatter(df, x='kapacitet', y='cijena_€', color='godina', size='kilometraža',
                 hover_data=['marka', 'model'], title='Odnos kapaciteta motora i cijene',
                 labels={'kapacitet': 'Kapacitet motora', 'cijena_€': 'Cijena (€)', 'kilometraža': 'Kilometraža'})

fig.update_layout(
    xaxis=dict(title_text='Kapacitet motora', tickvals=df['kapacitet'].unique(), ticktext=df['kapacitet'].unique())
)

fig.show()





*   Prvi scatter plot prikazuje odnos između godine proizvodnje automobila i njihove cijene. Postoji opći trend da noviji automobili imaju tendenciju biti skuplji. Ima više automobila nego skupih. Kako se krećemo prema novijim cgodina proizvodnje raspon cijena se širi.
*   Drugi plot prikazuje odnos između kapaciteta motora i cijene automobila. Postoji velika varijabilnost cijena unutar automobila sličnog kapaciteta motora, te se također čini da postoji nekoliko iznimno skupih automobila s različitim kapacitetima motora.



In [ ]:
# @title Distribucija tipova goriva i vrste transmisije u podacima

import plotly.graph_objects as go

from plotly.subplots import make_subplots

fig = make_subplots(rows=1, cols=2, subplot_titles=["Tip goriva", "Transmisija"])

fig.add_trace(go.Histogram(x=df["gorivo"], marker=dict(color="skyblue"), opacity=0.75), row=1, col=1)
fig.add_trace(go.Histogram(x=df["transmisija"], marker=dict(color="salmon"), opacity=0.75), row=1, col=2)

fig.update_layout(title_text="Interaktivni histogrami, prikazuju raznovrsnost i količinu automobila po nekim osobinama.", showlegend=False, bargap=0.2)

fig.update_xaxes(title_text="Tip goriva", row=1, col=1)
fig.update_yaxes(title_text="Count", row=1, col=1)
fig.update_xaxes(title_text="Transmisija", row=1, col=2)
fig.update_yaxes(title_text="Count", row=1, col=2)

fig.show()

In [ ]:
# @title Odnos kapaciteta motora i cijene, po transmisiji

import plotly.express as px

# Kreiranje interaktivnog scatter plot-a
fig = px.scatter(df, x='kapacitet', y='cijena_€', color='transmisija',
                 title='Scatter Plot - Odnos kapaciteta motora i cijene s transmisijom',
                 labels={'kapacitet': 'Kapacitet motora', 'cijena_€': 'Cijena (€)', 'transmisija': 'Transmisija'})

# Prikazivanje grafikona
fig.show()


Ovaj plot vizualizira odnos između kapaciteta motora i cijena automobila, te priakzuje kako se transmisija uklapa u taj odnos. Uočavamo da su automobili s automatskom transmisijom generalno ravnomjerno raspoređeni kroz cijeli raspon kapaciteta, s par outliera.

#Predviđanje

In [ ]:
# @title Instalacija potrebnih biblioteka

In [ ]:
# @title Import potrebnih biblioteka

from sklearn.ensemble import RandomForestRegressor
import seaborn as sns
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.preprocessing import OneHotEncoder
from sklearn.compose import make_column_transformer
from sklearn.pipeline import make_pipeline
from sklearn.metrics import r2_score
import numpy as np
import pandas as pd
import time


In [ ]:
# @title Proučavanje koliko su pojedini stupci bitni za predviđanje.

# Atributi za treniranje modela
X = df[["kilometraža", "kapacitet", "godina"]]

# X = df.select_dtypes(include=['number'])
# X = X.drop(columns="cijena_€")

# Ciljna varijabla koju želimo predviđati
y = df["cijena_€"]

# Inicijalizacija Random Forest Regressor modela
model = RandomForestRegressor()

# Treniranje modela na osnovu atributa X i ciljne varijable y
model.fit(X, y)

# Izračunavanje i ispisivanje važnosti atributa
feature_importances = pd.Series(model.feature_importances_, index=X.columns)
print("Važnost atributa:")
print(feature_importances)

Važnost atributa:
kilometraža    0.102931
kapacitet      0.214673
godina         0.682396
dtype: float64


In [ ]:
# Čuvanje DataFrame-a u CSV file
df.to_csv("prepped_car.csv")

In [ ]:
# Učitavanje podataka
X = df.drop(columns="cijena_€")
y = df["cijena_€"]

Pomoću "train_test_split" metode dijelimo podatke kako bi model mogli trenirati na jednom skupu podataka, a evaluirati, odnosno testirati na drugom. 20% podataka ide u testni skup, dok ostatak čini skup za trening.

In [ ]:
# Podjela podataka na trening i test skup
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2)

One-Hot Encoding koristimo za pretvorbu kategoričkih varijabli u binarne stupce.
"make_column_transformer" je funkcije iz "sklearn.compose" koja omogućuje primjenu transformacija na određene stupce, dok se ostali stupci prosljeđuju bez promjena.


In [ ]:
# Inicijalizacija OneHotEncoder objekta za enkodiranje kategoričkih promenljivih
ohe = OneHotEncoder()

In [ ]:
# Enkodiranje određenih kategoričkih stupaca
ohe.fit(X[["marka","model","gorivo","transmisija","kilometraža","godina","kapacitet"]])

OneHotEncoder()

In [ ]:
# Prikazivanje kategorija koje su korištene pri enkodiranju
ohe.categories_

[array(['Acura', 'Alfa Romeo', 'Audi', 'BMW', 'Buick', 'Cadillac', 'Chery',
        'Chevrolet', 'Chrysler', 'Citroen', 'Dacia', 'Daewoo', 'Dodge',
        'Fiat', 'Ford', 'Geely', 'Great Wall', 'Honda', 'Hyundai',
        'Infiniti', 'Iveco', 'Jaguar', 'Jeep', 'Kia', 'LADA', 'Lancia',
        'Land Rover', 'Lexus', 'Lifan', 'Lincoln', 'Mazda',
        'Mercedes-Benz', 'Mini', 'Mitsubishi', 'Nissan', 'Opel', 'Peugeot',
        'Pontiac', 'Porsche', 'Renault', 'Rover', 'Saab', 'Seat', 'Skoda',
        'SsangYong', 'Subaru', 'Suzuki', 'Toyota', 'Volkswagen', 'Volvo',
        'ВАЗ', 'ГАЗ', 'ЗАЗ', 'Москвич', 'УАЗ'], dtype=object),
 array(['100', '1007', '100NX', ..., 'М5', 'Соболь', 'Таврия'],
       dtype=object),
 array([0, 1, 2, 3, 4, 5]),
 array(['automatic', 'mechanical'], dtype=object),
 array([0.0e+00, 1.0e+00, 2.0e+00, 3.0e+00, 4.0e+00, 5.0e+00, 6.0e+00,
        7.0e+00, 9.0e+00, 1.0e+01, 1.1e+01, 1.3e+01, 2.0e+01, 2.3e+01,
        2.5e+01, 4.6e+01, 4.9e+01, 5.0e+01, 6.0e+01, 6.6e+

In [ ]:
# Pravljenje ColumnTransformer objekta za enkodiranje određenih stupaca
column_trans = make_column_transformer(
    (OneHotEncoder(categories=ohe.categories_), ["marka", "model", "gorivo", "transmisija", "kilometraža", "godina", "kapacitet"]),
    remainder="passthrough"
)

Kao model za predviđanje koristimo linearnu regresiju.
Koristimo "pipeline" kako bi kombinirali korake pretprocesiranja podataka s konačnim korakom modeliranja.
Pipeline koristimo kako bi kod bio jednostavniji i čišći, te kako bi predviđanje kasnije bilo jednostavnije za pristupiti.

In [ ]:
# Inicijalizacija linearne regresije
lr = LinearRegression()

In [ ]:
# Pravljenje pipelina koji uključuje enkodiranje i model regresije
pipe = make_pipeline(column_trans, lr)

In [ ]:
# Treniranje modela na trening podacima
pipe.fit(X_train, y_train)

Pipeline(steps=[('columntransformer',
                 ColumnTransformer(remainder='passthrough',
                                   transformers=[('onehotencoder',
                                                  OneHotEncoder(categories=[array(['Acura', 'Alfa Romeo', 'Audi', 'BMW', 'Buick', 'Cadillac', 'Chery',
       'Chevrolet', 'Chrysler', 'Citroen', 'Dacia', 'Daewoo', 'Dodge',
       'Fiat', 'Ford', 'Geely', 'Great Wall', 'Honda', 'Hyundai',
       'Infiniti', 'Iveco', 'Jaguar', 'Jeep', 'K...
       1.1       , 1.2       , 1.3       , 1.4       , 1.5       ,
       1.6       , 1.7       , 1.8       , 1.9       , 2.        ,
       2.05516111, 2.1       , 2.2       , 2.3       , 2.4       ,
       2.5       , 2.6       , 2.7       , 2.8       , 2.9       ,
       3.        , 3.1       , 3.2       , 3.3       , 3.4       ,
       3.5       , 3.6       , 3.7       , 3.8       , 3.9       ,
       4.        , 4.1       , 4.2       , 4.3       , 4.4       ,
       4.5       , 4.6       , 4.7       , 4.8       , 4.9       ,
       5.        , 5.2       , 5.3       , 5.4       , 5.461     ,
       5.5       , 5.6       , 5.7       , 5.8       , 5.9       ,
       6.        , 6.2       , 6.3       , 6.4       , 6.8       ,
       7.5       , 8.        ])]),
                                                  ['marka', 'model', 'gorivo',
                                                   'transmisija', 'kilometraža',
                                                   'godina', 'kapacitet'])])),
                ('linearregression', LinearRegression())])

In [ ]:
# Predikcija cijena na test podacima
y_pred = pipe.predict(X_test)

In [ ]:
# Računanje R^2 skora za procjenu performansi modela
r2_score(y_test, y_pred)

0.8652934996671601

Kod zatim ponavlja proces dijeljenja podataka, treniranja modela i evaluacije modela 10 puta, svaki put s različitim random_state za train_test_split, što osigurava različite podjele podataka svaki put. Tijekom svake iteracije, model se trenira i evaluira koristeći koeficijent determinacije (R² score) koji mjeri koliko dobro predviđanja modela odgovaraju stvarnim podacima.

In [ ]:
# Prikupljanje i ispis R^2 rezultata za različite podjele trening i test skupova
scores = []

start_time = time.time()

for i in range(100):
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=i)
    lr = LinearRegression()
    pipe = make_pipeline(column_trans, lr)
    pipe.fit(X_train, y_train)
    y_pred = pipe.predict(X_test)
    print(r2_score(y_test, y_pred), i)
    scores.append(r2_score(y_test, y_pred))

end_time = time.time()

print("Total time taken: {:.2f} seconds".format(end_time - start_time))

0.8618203459590879 0
0.8645783355680584 1
0.8667478964646006 2
0.8627008578114863 3
0.868476247567123 4
0.8730003320543538 5
0.8688696969888057 6
0.8664089459579583 7
0.8714855915517364 8
0.8686670427139273 9
0.8679022732588271 10
0.8784524453172662 11
0.8780728996693865 12
0.8739959313502385 13
0.8720282879842434 14
0.8615221491981881 15
0.8755632971004843 16
0.868046530239579 17
0.8647051420143576 18
0.8605174141714914 19
0.8687960877317897 20
0.8684391830897098 21
0.8703228327216075 22
0.8664356781372852 23
0.8678821180979839 24
0.8656220984819533 25
0.8688261293575332 26
0.8680515890573499 27
0.866134127740336 28
0.8634799100231617 29
0.872106542810908 30
0.8679022642139326 31
0.8697371521829023 32
0.8644211496457167 33
0.8727033221890876 34
0.859374571941675 35
0.8657834699770679 36
0.8639033343244974 37
0.8723322086403206 38
0.8694656696869929 39
0.8671298359034189 40
0.8760205696477816 41
0.8636790839278847 42
0.8651049484242941 43
0.8672679992371153 44
0.8634514369725881 45
0.8

Ovaj proces se izvršio na GPU Runtimeu, te je vrijeme izvođenja smanjeno za oko 40%. Ovaj isječak koda je dosta zahtjevan stoga je bilo logično ubrzati ga mijenjanjem hardvera.

In [ ]:
# Pronalaženje najbolje podjele
best_index = np.argmax(scores)
best_score = scores[best_index]
print(f"Najbolji R^2 rezultat: {best_index}: {best_score}")

Najbolji R^2 rezultat: 91: 0.8807481935956667


In [ ]:
# Ponovno treniranje modela na skupu podataka sa najboljim rezultatom
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=best_index)
lr = LinearRegression()
pipe = make_pipeline(column_trans, lr)
pipe.fit(X_train, y_train)

y_pred=pipe.predict(X_test)
print(r2_score(y_test,y_pred))

0.8807481935956667


In [ ]:
# Predikcija cijena za novi skup podataka
# engine_fuel_mapping={"gasoline":0,"gas":1,"diesel":2,"hybrid-petrol":3,"hybrid-diesel":4,"electric":5}
# new_data_prediction = pipe.predict(pd.DataFrame([['Nissan','Primera',2003,160000,2,"mechanical",1.6]], columns=["marka","model","godina","kilometraža","gorivo","transmisija","kapacitet"]))
# print(new_data_prediction)

# @title Predikcija cijena za novi skup podataka
marka = 'Nissan' # @param {type:"string"}
model = 'Primera' # @param {type:"string"}
godina = 2007 # @param {type:"integer"}
kilometraza = 165672 # @param {type:"number"}
gorivo = "diesel" # @param ["gasoline", "gas", "diesel", "hybrid-petrol", "hybrid-diesel", "electric"]
transmisija = "mechanical" # @param ["mechanical", "automatic"]
kapacitet = 1.6 # @param {type:"number"}

gorivo = engine_fuel_mapping[gorivo]
kilometraza=round_to_first_two_digits(kilometraza)
gorivo

# Predikcija cijena za novi skup podataka
new_data_prediction = pipe.predict(pd.DataFrame([[marka, model, godina, kilometraza, gorivo, transmisija, kapacitet]], columns=["marka","model","godina","kilometraža","gorivo","transmisija","kapacitet"]))
print(np.round(new_data_prediction, 2))

[5475.37]


#Web Scraping

In [ ]:
# @title Import potrebnih biblioteka

import requests
from bs4 import BeautifulSoup

from bs4.element import Tag

In [ ]:
# @title Početne postavke
url = "https://www.oglasnik.hr/prodaja-automobila?ad_params_7_1%5B%5D=832&ad_params_9_from=1&ad_params_8_to=2019"
Model = 'Nissan'

In [ ]:
# @title Izdvajanje svih modela gdje je traženi proizdođač (Nissan) iz naše liste podataka
models = df.loc[df['marka'] == Model, 'model'].unique()

# Ispisivanje rezultata
print("Modeli automobila marke Nissan:")
print(models)

Modeli automobila marke Nissan:
['Qashqai' 'Serena' 'Almera' 'Almera Tino' 'Primera' 'Terrano' 'Juke'
 'X-Trail' 'Patrol' 'Murano' 'Pixo' 'Qashqai+2' 'Micra' 'Titan'
 'Pathfinder' 'Tiida' 'Leaf' 'Teana' 'Note' 'Sunny' 'Maxima' 'Sentra'
 'Bluebird' 'NV S' 'Altima' 'Navara' 'Rogue' 'Quest' 'Vanette' 'Armada'
 'Interstar' 'Pulsar' '100NX' 'Primastar' 'Versa' 'L50' '200SX' 'Prairie'
 'Cabstar' 'Urvan' 'NV200' '350Z' 'Skyline' 'Frontier']


In [ ]:
# @title Funkcija za učitavanje url-a

def get_soup_from_url(url):
    try:
        # Dohvaćanje HTML sadržaja stranice
        response = requests.get(url)
        response.raise_for_status()  # Raise an HTTPError for bad responses

        # Parsiranje HTML-a s BeautifulSoup
        soup = BeautifulSoup(response.text, 'html.parser')
        return soup
    except requests.exceptions.RequestException as e:
        print(f"Error fetching content from {url}: {e}")
        return None


In [ ]:
# @title Učitavanje početne stranice
soup = get_soup_from_url(url)

In [ ]:
# @title Učitavanje "stranica" automobila

# Pronalaženje svih elemenata a s određenim klasama
pages = soup.find_all('ul', class_='pagination pagination-md')
pages

[<ul class="pagination pagination-md"><li class="edge disabled" data-first=""><span><span class="fa fa-angle-double-left fa-fw"></span></span></li><li class="edge disabled" data-previous=""><span><span class="fa fa-angle-left fa-fw"></span></span></li><li class="active" data-page="1" data-pages=""><span>1</span></li><li data-page="2" data-pages=""><a href="https://www.oglasnik.hr/prodaja-automobila?ad_params_7_1%5B0%5D=832&amp;ad_params_9_from=1&amp;ad_params_8_to=2019&amp;page=2">2</a></li><li class="edge" data-next="" data-page="2"><a data-page="2" href="https://www.oglasnik.hr/prodaja-automobila?ad_params_7_1%5B0%5D=832&amp;ad_params_9_from=1&amp;ad_params_8_to=2019&amp;page=2" title="Sljedeća"><span class="fa fa-angle-right fa-fw"></span></a></li><li class="edge" data-last="" data-page="2"><a href="https://www.oglasnik.hr/prodaja-automobila?ad_params_7_1%5B0%5D=832&amp;ad_params_9_from=1&amp;ad_params_8_to=2019&amp;page=2"><span class="fa fa-angle-double-right fa-fw"></span></a></l

In [ ]:
# @title Dohvaćanje ostalih "stranica" automobila

# Inicijalizacija prazne liste linkova
url_list = []
url_list.append(url)

# Inicijalizacija BeautifulSoup objekta na prazan string
soup_list = []

for page in pages:
    # Find all links within the current page element
    page_links = page.find_all('a', href=True)

    # Extract and print the href attributes from each link
    for link in page_links:
        href_link = link['href']
        # print(f"Href link: {href_link}")
        url_list.append(href_link)


url_list = set(url_list)

for urls in url_list:
  print(urls)
  soup_list.append(get_soup_from_url(urls))

https://www.oglasnik.hr/prodaja-automobila?ad_params_7_1%5B0%5D=832&ad_params_9_from=1&ad_params_8_to=2019&page=2
https://www.oglasnik.hr/prodaja-automobila?ad_params_7_1%5B%5D=832&ad_params_9_from=1&ad_params_8_to=2019


In [ ]:
# @title # Inicijalizacija zajedničkog BeautifulSoup objekta

# Inicijalizacija praznog dokumenta
combined_html = ""

# Pretvaranje svakog soup objekta u HTML i spajanje
for soup_obj in soup_list:
    if soup_obj:
        combined_html += soup_obj.prettify()

# Inicijalizacija zajedničkog BeautifulSoup objekta
soup = BeautifulSoup(combined_html, 'html.parser')

In [ ]:
# @title Klasa Automobil

class Automobil:
    def __init__(self, container, href, naziv, proizvodac="Nissan", model=None, transmisija=None, kilometraza=None, godina=None, gorivo=None, zapremina_motora=None, cijena=None, kapacitet=None):
        self.href = href
        self.naziv = naziv
        self.proizvodac = proizvodac
        self.model = model
        self.transmisija = transmisija
        self.kilometraza = kilometraza
        self.godina = godina
        self.gorivo = gorivo
        self.zapremina_motora = zapremina_motora
        self.cijena = cijena
        self.kapacitet = kapacitet

In [ ]:
# @title Usporedba naših i dohvaćenih modela

# Pronalaženje svih elemenata a s određenim klasama
a_elements = soup.find_all('a', class_='classified-box classified-box-wide no-hover no-checkbox category-listing clearfix izdvojeno-osnovni')

# Inicijalizacija prazne liste za spremanje rezultata
AutomobiliOsnovno = []

# Dohvaćanje potrebnih elemenata
for element in a_elements:
    href_link = element.get('href')

    h3_elements = element.find_all('h3', class_='classified-title') #hohvatit samo prvi h3?
    for h3_element in h3_elements:
        tekst_naslova = h3_element.text
        # print(f"Tekst naslova: {tekst_naslova}")

        # Provjera da li je neki model iz liste nissan_models sadržan u tekstu naslova
        #Tekna+ - objasnit
        for model in models:
            if model.lower() in tekst_naslova.lower():
                # Dodavanje pronađenog modela u klasu Automobil
                automobil = Automobil(container='', href=href_link, naziv=tekst_naslova)
                AutomobiliOsnovno.append(automobil)

# Ispisivanje rezultata
for automobil in AutomobiliOsnovno:
    print(f"Naziv: {automobil.naziv}, Href: {automobil.href}")


Naziv: 
              Nissan Qashqai 1,5 dCi ALU NAVI KAMERA LED *GARANC* 69.000
             , Href: https://www.oglasnik.hr/prodaja-automobila/nissan-qashqai-1-5-dci-alu-navi-kamera-led-garanc-69-000-oglas-5485641
Naziv: 
              Nissan Micra 1.0
             , Href: https://www.oglasnik.hr/prodaja-automobila/nissan-micra-1-0-oglas-5417273
Naziv: 
              Nissan X-Trail 1,6 dCi N-Connecta ALU NAVI LED TEMPOMAT
             , Href: https://www.oglasnik.hr/prodaja-automobila/nissan-x-trail-1-6-dci-n-connecta-alu-navi-led-tempomat-oglas-5398637
Naziv: 
              NISSAN QASHQAI 1.5 DCI BUSINESS EDITION-JAMSTVO, 19.490,00 €
             , Href: https://www.oglasnik.hr/prodaja-automobila/nissan-qashqai-1-5-dci-business-edition-jamstvo-19-490-00-oglas-5395234
Naziv: 
              NISSAN QASHQAI 1.5 DCI BUSINESS EDITION - JAMSTVO 15 MJESECI, 18.900,00 € -...
             , Href: https://www.oglasnik.hr/prodaja-automobila/nissan-qashqai-1-5-dci-business-edition-jamstvo-15-mje

In [ ]:
# @title Funkcija za mapiranje svojstva

def naslov_u_svojstvo(naslov):
    mapping = {
        'Proizvođač': 'proizvodac',
        'Model': 'model',
        'Godina proizvodnje': 'godina',
        'Kilometraža': 'kilometraza',
        'Radni obujam': 'zapremina_motora',
        'Vrsta goriva': 'gorivo',
        'Vrsta mjenjača': 'transmisija',
        'Kapacitet': 'kapacitet',
    }
    # Dodajte dodatne varijacije naslova koje možete susresti
    if naslov.startswith('Proizvođač'):
        return mapping.get('Proizvođač', 'proizvodac')
    elif naslov.startswith('Model'):
        return mapping.get('Model', 'model')
    elif naslov.startswith('Godina proizvodnje'):
        return mapping.get('Godina proizvodnje', 'godina')
    elif naslov.startswith('Kilometraža'):
        return mapping.get('Kilometraža', 'kilometraza')
    elif naslov.startswith('Radni obujam'):
        return mapping.get('Radni obujam', 'zapremina_motora')
    elif naslov.startswith('Vrsta goriva'):
        return mapping.get('Vrsta goriva', 'gorivo')
    elif naslov.startswith('Vrsta mjenjača'):
        return mapping.get('Vrsta mjenjača', 'transmisija')
    elif naslov.startswith('Kapacitet'):
        return mapping.get('Kapacitet', 'kapacitet')
    else:
        # Ako naslov nije pronađen u mapi, koristi lowercased verziju naslova
        return naslov.lower()

In [ ]:
# @title Funkcija za predviđanje cijena

import re

def predict_price(auto):
    try:
      marka = Model
      model = auto.model
      godina = auto.godina
      kilometraza = auto.kilometraza
      gorivo = auto.gorivo
      transmisija = auto.transmisija
      kapacitet = auto.kapacitet
    except Exception as e:
            print(f"Greška prilikom dohvaćanja vrijednosti: {e}")
            return
    # try:
    #   marka = Model
    #   model = auto.model if auto.model is not None else 'Juke'
    #   godina = int(auto.godina) if auto.godina is not None else 2017
    #   kilometraza = int(re.search(r'\b(\d+)\b', str(auto.kilometraza)).group(1)) if auto.kilometraza is not None and re.search(r'\b(\d+)\b', str(auto.kilometraza)) else 0
    #   gorivo = engine_fuel_mapping[auto.gorivo] if auto.gorivo is not None and auto.gorivo in engine_fuel_mapping else 1
    #   transmisija = auto.transmisija if auto.transmisija is not None else 'mechanical'
    #   kapacitet = auto.kapacitet if auto.kapacitet is not None else 0.0
    # except Exception as e:
    #         print(f"Greška prilikom dohvaćanja vrijednosti: {e}")
    #         return

    try:
      # Predviđanje cijene za novi skup podataka
      new_data_prediction = pipe.predict(pd.DataFrame([[marka, model, godina, kilometraza, gorivo, transmisija, kapacitet]],
                                                      columns=["marka", "model", "godina", "kilometraža", "gorivo", "transmisija", "kapacitet"]))

      # Zaokruživanje rezultata na dvije decimale
      rounded_prediction = np.round(new_data_prediction, 2)

      print("Predviđena cijena:", rounded_prediction)

    except Exception as e:
      column_names = ["marka","model","gorivo","transmisija","kilometraža","godina","kapacitet"]
      error_message = str(e)  # Pretvaranje objekta pogreške u string
      error_message = error_message.replace("column 6", column_names[6])
      error_message = error_message.replace("column 5", column_names[5])
      error_message = error_message.replace("column 4", column_names[4])
      error_message = error_message.replace("column 3", column_names[3])
      error_message = error_message.replace("column 2", column_names[2])
      error_message = error_message.replace("column 1", column_names[1])
      error_message = error_message.replace("column 1", column_names[0])
      print(f"Greška prilikom predviđanja cijene: {error_message}")

In [ ]:
# @title Spremanje podataka u klasu

# Inicijalizacija prazne liste za spremanje rezultata
Automobili = []

auto_predikcija = AutomobiliOsnovno
# auto_predikcija = AutomobiliOsnovno[:5]

for auto in auto_predikcija:
    print("\nAUTOMOBIL\n")
    auto_url = auto.href

    auto_soup = get_soup_from_url(auto_url)

    stranice = auto_soup.find_all('div', class_='site-wrapper position-relative pad-xs-only-lr')

    for stranica in stranice:
        podaci_o_vozilu = stranica.find('div', class_='col-md-12 oglas-details')

        if podaci_o_vozilu:
            print("Podaci o vozilu:")

            model_element  = auto_soup.find('h1', class_='h2-like no-top-margin color-light-blue')
            model = model_element.text.strip()
            print(model)

            price_element  = auto_soup.find('dd')
            price_text = price_element.get_text(strip=True)
            # numeric_part = re.sub(r'\D', '', price_text)

            spanovi = podaci_o_vozilu.find_all('span', class_='color-light')
            # print(spanovi)

            # Automobili.append(automobil)
            # Stvori novu instancu automobila prije petlje kako bi bila dostupna unutar petlje
            automobil = Automobil(container='', href=auto_url, naziv=model, cijena=price_text)  # Postavi početne vrijednosti
            # automobil = Automobil(container='', href=auto_url, naziv=model, cijena=int(numeric_part))  # Postavi početne vrijednosti
            for span_element in spanovi:
                naslov = span_element.text.strip()
                # print("Naslov:", naslov)

                # Provjeri postoji li sljedeći sibling element nakon <span>
                br_sibling = span_element.find_next_sibling('br')

                # Provjeri postoji li sljedeći sibling element i je li tipa Tag
                if br_sibling and isinstance(br_sibling, Tag):
                    # Dohvati tekst između <span> i <br>
                    tekst_izmedju = br_sibling.previous_sibling.strip()
                    # print("Vrijednost:", tekst_izmedju)

                else:
                    # print("Nije pronađen sljedeći sibling element nakon <span> ili nije tipa Tag.")
                    ul_sibling = span_element.find_next_sibling('ul')

                    if ul_sibling and ul_sibling.name == 'ul':
                        # print("Sljedeći sibling element je <ul>.")
                        if ul_sibling and ul_sibling.name == 'ul':
                          # Pronađi sve <li> elemente unutar <ul>
                          li_elements = ul_sibling.find_all('li')

                          # Iteriraj kroz <li> elemente i dohvati tekst
                          for li_element in li_elements:
                            tekst_iz_li = li_element.get_text(strip=True)
                            # print("Tekst iz <li>:", tekst_iz_li)
                            tekst_izmedju = tekst_iz_li

                svojstvo = naslov_u_svojstvo(naslov)
                print(f"\n !!! Postavljanje - {naslov} - {svojstvo} = {tekst_izmedju}")
                setattr(automobil, svojstvo, tekst_izmedju)

            Automobili.append(automobil)




AUTOMOBIL

Podaci o vozilu:
Nissan Qashqai 1,5 dCi ALU NAVI KAMERA LED *GARANC* 69.000

 !!! Postavljanje - Proizvođač: - proizvodac = Nissan

 !!! Postavljanje - Model: - model = Qashqai

 !!! Postavljanje - Godina proizvodnje: - godina = 2018

 !!! Postavljanje - Kilometraža: - kilometraza = 69182 km

 !!! Postavljanje - Snaga motora: - snaga motora: = 81 kW

 !!! Postavljanje - Radni obujam: - zapremina_motora = 1461 cm3

 !!! Postavljanje - Vrsta goriva - gorivo = dizel

 !!! Postavljanje - Stanje vozila - stanje vozila = odlično

 !!! Postavljanje - Broj brzina - broj brzina = 6 brzina

 !!! Postavljanje - Vrsta mjenjača - transmisija = ručni mjenjač

 !!! Postavljanje - Oblik karoserije - oblik karoserije = terenac/suv

 !!! Postavljanje - Broj vrata - broj vrata = 5

 !!! Postavljanje - Boja - boja = siva

 !!! Postavljanje - Pogon - pogon = prednji

 !!! Postavljanje - Klima uređaj - klima uređaj = automatska

 !!! Postavljanje - Vlasnik - vlasnik = 1

 !!! Postavljanje - Airb

In [ ]:
# @title Funkcija za ispravljanje vrijednosti

#kat_godine = df['godina'].unique()

def ispravi_vrijednosti(auto):
    auto.kilometraza = int(re.search(r'\b(\d+)\b', str(auto.kilometraza)).group(1)) if auto.kilometraza is not None and re.search(r'\b(\d+)\b', str(auto.kilometraza)) else 0
    auto.kilometraza = round_to_first_two_digits(auto.kilometraza)

    if isinstance(auto.godina, str) and '.' in auto.godina:
        auto.godina = auto.godina.replace('.', '')
    auto.godina = int(auto.godina)
    #auto.godina = pd.cut(auto.godina, bins=kat_godine, labels=labels, right=False)

    if auto.kapacitet is None:
      auto.kapacitet= 2.0

    auto.gorivo = engine_fuel_mapping[auto.gorivo] if auto.gorivo is not None and auto.gorivo in engine_fuel_mapping else 1

    numeric_part = re.sub(r'\D', '', auto.cijena)
    auto.cijena = int(numeric_part)

    if auto.transmisija is not None:
      # Provjeri sadrži li tekst riječ "automatski"
      if 'automatski' in auto.transmisija.lower():
          auto.transmisija = 'automatic'
      else:
          auto.transmisija = 'mechanical'
    else:
       auto.transmisija = 'mechanical'



In [ ]:
# @title Ispis i obrada podataka

for index, automobil in enumerate(Automobili):
  ispravi_vrijednosti(automobil)

print(f"Ukupno automobila: {len(Automobili)} ")

# Pretvorba niza instanci klase Automobil u DataFrame
df_auto = pd.DataFrame([vars(auto) for auto in Automobili])

# Ispis DataFrame-a
# df_auto
df_auto[['proizvodac', 'model', 'transmisija', 'kilometraza', 'godina', 'gorivo', 'kapacitet', 'cijena']]

Ukupno automobila: 24 


proizvodac    model transmisija  kilometraza  godina  gorivo  kapacitet  \
0      Nissan  Qashqai  mechanical        69000    2018       1        2.0   
1      Nissan    Micra  mechanical        68000    2019       1        2.0   
2      Nissan  X-Trail  mechanical       160000    2017       1        2.0   
3      Nissan     None  mechanical       110000    2019       1        2.0   
4      Nissan     None  mechanical       100000    2019       1        2.0   
5      Nissan     Juke  mechanical        68000    2016       1        2.0   
6      Nissan  X-Trail  mechanical       320000    2014       1        2.0   
7      Nissan   Patrol  mechanical       120000    2007       1        2.0   
8      Nissan     None  mechanical       200000    1997       1        2.0   
9      Nissan  Terrano  mechanical       180000    1988       1        2.0   
10     Nissan  Qashqai  mechanical        56000    2018       1        2.0   
11     Nissan  X-Trail  mechanical       200000    2017       1        2.0   
12     Nissan     Note  mechanical        52000    2016       1        2.0   
13     Nissan  X-Trail   automatic       180000    2016       1        2.0   
14     Nissan    Micra  mechanical        86000    2017       1        2.0   
15     Nissan  Primera  mechanical       370000    2002       1        2.0   
16     Nissan  Qashqai  mechanical       240000    2014       1        2.0   
17     Nissan    Sunny  mechanical       360000    1995       1        2.0   
18     Nissan     Juke  mechanical        70000    2018       1        2.0   
19     Nissan  Qashqai  mechanical       130000    2016       1        2.0   
20     Nissan  Qashqai  mechanical       120000    2019       1        2.0   
21     Nissan  Qashqai   automatic        94000    2015       1        2.0   
22     Nissan    Micra  mechanical        50000    2018       1        2.0   
23     Nissan  Qashqai  mechanical       100000    2019       1        2.0   

    cijena  
0    19200  
1     9900  
2    17500  
3    19490  
4    18900  
5    13900  
6    10900  
7     1500  
8     1200  
9     1600  
10   19700  
11   16500  
12    7900  
13   17900  
14    8150  
15    2200  
16   12500  
17     600  
18   14000  
19   15500  
20   19900  
21   17900  
22   10500  
23   20500

In [ ]:
# @title Predvidanje cijena
for index, automobil in enumerate(Automobili):
  print(f"  ({index}) {automobil.proizvodac} - {automobil.model}: {np.round(automobil.cijena, 2)} €")
  predict_price(automobil)
  print(vars(automobil))
  print()

  (0) Nissan - Qashqai: 19200 €
Predviđena cijena: [18769.26]
{'href': 'https://www.oglasnik.hr/prodaja-automobila/nissan-qashqai-1-5-dci-alu-navi-kamera-led-garanc-69-000-oglas-5485641', 'naziv': 'Nissan Qashqai 1,5 dCi ALU NAVI KAMERA LED *GARANC* 69.000', 'proizvodac': 'Nissan', 'model': 'Qashqai', 'transmisija': 'mechanical', 'kilometraza': 69000, 'godina': 2018, 'gorivo': 1, 'zapremina_motora': '1461 cm3', 'cijena': 19200, 'kapacitet': 2.0, 'snaga motora:': '81 kW', 'stanje vozila': 'odlično', 'broj brzina': '6 brzina', 'oblik karoserije': 'terenac/suv', 'broj vrata': '5', 'boja': 'siva', 'pogon': 'prednji', 'klima uređaj': 'automatska', 'vlasnik': '1', 'airbag': 'prednji i bočni', 'servisna knjižica': 'Da', 'novo/rabljeno': 'Rabljeno'}

  (1) Nissan - Micra: 9900 €
Predviđena cijena: [20904.67]
{'href': 'https://www.oglasnik.hr/prodaja-automobila/nissan-micra-1-0-oglas-5417273', 'naziv': 'Nissan Micra 1.0', 'proizvodac': 'Nissan', 'model': 'Micra', 'transmisija': 'mechanical', 'k